In [22]:
import sys, json
sys.path.insert(1, '../data_collection')
from collection import *

import pandas as pd
import plotly.graph_objects as go
import numpy as np
from plotly.subplots import make_subplots
import plotly.express as px

In [77]:
df_gtemp = pd.read_csv('global_temp.csv')
df_gtemp['date'] = pd.to_datetime(df_gtemp['date'])

with open('../data_collection/countries.json', 'r', encoding = 'latin1') as f:
    countries_json = json.load(f)
country_alpha3 = [[country, countries_json[country]['alpha3']] for country in countries_json.keys()]
df_country_alpha3 = pd.DataFrame(country_alpha3, columns = ['country', 'alpha3'])
df_gtemp = df_gtemp.merge(df_country_alpha3, on = 'country')

df_gtemp = df_gtemp[df_gtemp.date.dt.year > 1849]
df_gtemp['yearly_mean'] = df_gtemp.groupby(by = ['country', df_gtemp.date.dt.year])['monthly_anomaly'].transform('mean')
df_gtemp_yearly = df_gtemp.groupby(by = ['country', df_gtemp.date.dt.year]).first().drop(columns = ['date', 'monthly_anomaly']).reset_index()
yearly_min = df_gtemp_yearly.loc[:, 'yearly_mean'].min()
yearly_max = df_gtemp_yearly.loc[:, 'yearly_mean'].max()
df_gtemp_yearly

country  date alpha3  yearly_mean
0      Afghanistan  1850    AFG    -0.734750
1      Afghanistan  1851    AFG    -0.455167
2      Afghanistan  1852    AFG    -0.519667
3      Afghanistan  1853    AFG    -0.605000
4      Afghanistan  1854    AFG    -0.455083
...            ...   ...    ...          ...
33167     Zimbabwe  2009    ZWE     0.207250
33168     Zimbabwe  2010    ZWE     0.816250
33169     Zimbabwe  2011    ZWE     0.432417
33170     Zimbabwe  2012    ZWE     0.351333
33171     Zimbabwe  2013    ZWE     0.700750

[33172 rows x 4 columns]

In [3]:
print('min: ', yearly_min)
print('max: ', yearly_max)

min:  -2.9531666666666667
max:  3.0295833333333335


In [78]:
fig = px.choropleth(data_frame = df_gtemp_yearly,
                    title = '<br>Global Temperature',
                    locations = 'alpha3',
                    color = 'yearly_mean',  # value in column 'Confirmed' determines color
                    hover_name = 'country',
                    color_continuous_scale = 'Jet',  #  color scale red, yellow green
                    range_color = [yearly_min, yearly_max],
                    animation_frame = 'date',
                    width = 1400, 
                    height = 1000)

fig.update_layout(
    margin = dict(l = 70, r = 70, t = 20, b = 0, pad = 4),
    paper_bgcolor = 'LightSteelBlue',
    title_font_size = 50, 
    coloraxis_colorbar = dict(
        title = 'Berkeley Earth<br>Temperature',
        thicknessmode = 'pixels', thickness = 40,
        lenmode = 'pixels', len = 620,
        ticks = 'outside', 
        ticksuffix = r' °C',
        dtick = 1),
    title = {
        "yref": "paper",
        "y" : 1,
        "yanchor" : "bottom"})

s = r': countrywise relative °C<br>    Jan 1951-Dec 1980<br>    average nullified'
fig.show()

In [5]:
afg = df_gtemp[df_gtemp.loc[:, 'country'] == 'Afghanistan']
fig = go.Figure(data=go.Scatter(x = afg['date'], y = afg['monthly_anomaly']))
fig.show()